In [1]:
import numpy as np
import cv2
import sys
np.set_printoptions(threshold=sys.maxsize)

In [2]:
cap = cv2.VideoCapture('./train/trainGray.mp4')
frameCount = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
frameWidth = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
frameHeight = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))

# buf = np.empty((frameCount, frameHeight, frameWidth), np.dtype('uint8'))
bufTemp = np.empty((frameCount, frameHeight * frameWidth), np.dtype('uint8'))

fc = 0
ret = True

# print(buf[fc].shape)
# print(np.array(cap.read())[1].shape)
# x = np.array(cap.read())[1]
# print(x[:,:,0].shape)

while (fc < frameCount  and ret):
#     ret, x = np.array(cap.read())
    ret, x = np.array(cap.read())
#     buf[fc] = x[:,:,0]
    x = x[:,:,0]
    x.shape = frameHeight*frameWidth
    bufTemp[fc] = x
    fc += 1

cap.release()

x = bufTemp[0, 0:frameHeight*frameWidth]
x.shape = (frameHeight, frameWidth)

In [3]:
y = np.loadtxt('./train/train.txt', np.dtype('float'))
theta = np.zeros(((frameHeight*frameWidth)+1), np.dtype('int16'))
# m = frameHeight*frameWidth
m = frameCount-1
lmbda = .01
alpha = .01
loopCount = 5
costArr = np.zeros(loopCount, np.dtype('float'))

In [4]:
for i in range(loopCount):
    cost = 0
    for j in range(1,frameCount):
        firstFrame = np.array(bufTemp[j-1], dtype='int16')
        secondFrame = np.array(bufTemp[j], dtype='int16')
        x = np.empty(((frameHeight*frameWidth)+1), np.dtype('int16'))
        x[0] = 1
        x[1:(frameHeight*frameWidth)+1] = secondFrame - firstFrame
        x = np.absolute(x)
        mean = np.mean(x)
        x = x - mean
        x = x/np.std(x)
#         grad = np.sum((np.dot(x, theta) - y[i])*x)/m
        grad = ((np.dot(x, theta) - y[j])*x)/m
        grad[1:len(grad)] = grad[1:len(grad)] + ((lmbda/m)*theta[1:len(theta)])
        cost = cost + ((np.dot(x, theta) - y[j])**2)/2
        theta = theta - (alpha*grad)
#     for j in range(1,frameCount):
#         firstFrame = np.array(bufTemp[j-1], dtype='int16')
#         secondFrame = np.array(bufTemp[j], dtype='int16')
#         x = np.empty(((frameHeight*frameWidth)+1), np.dtype('int16'))
#         x[0] = 1
#         x[1:(frameHeight*frameWidth)+1] = secondFrame - firstFrame
#         mean = np.mean(x)
#         x = x - mean
#         x = x/np.std(x)
#         cost = cost + (((np.dot(x, theta) - y[j])**2)/2)
    
    print(i)
    costArr[i] = cost/(2*m)
print(costArr)

0
1
2
3
4
[2.15685577 1.60758375 1.4533589  1.34064044 1.25003128]


In [5]:
result = np.empty((frameCount), np.dtype('float'))

for j in range(1,frameCount):
    firstFrame = np.array(bufTemp[j-1], dtype='int16')
    secondFrame = np.array(bufTemp[j], dtype='int16')
    x = np.empty(((frameHeight*frameWidth)+1), np.dtype('int16'))
    x[0] = 1
    x[1:(frameHeight*frameWidth)+1] = secondFrame - firstFrame
    x = np.absolute(x)
    mean = np.mean(x)
    x = x - mean
    x = x/np.std(x)
    result[j-1] = np.dot(x,theta)
    
result.tofile('./train/train2.txt',sep="\n",format="%s")

In [7]:
cost2 = 0
for j in range(1,frameCount):
    cost2 = cost2 + (((result[j-1] - y[j])**2)/2)

cost2 = cost2/(2*m)
print(cost2)

15.741795713055234


In [6]:
cost = 0
for j in range(1,frameCount):
    firstFrame = np.array(bufTemp[j-1], dtype='int16')
    secondFrame = np.array(bufTemp[j], dtype='int16')
    x = np.empty(((frameHeight*frameWidth)+1), np.dtype('int16'))
    x[0] = 1
    x[1:(frameHeight*frameWidth)+1] = secondFrame - firstFrame
    x = np.absolute(x)
    mean = np.mean(x)
    x = x - mean
    x = x/np.std(x)
    cost = cost + (((np.dot(x, theta) - y[j])**2)/2)

cost = cost/(2*m)
print(cost)

15.741795713055234


In [8]:
theta

array([-4.62107070e-04, -3.08237017e-04, -3.01102652e-04, -3.27416740e-04,
       -3.09883305e-04, -3.25689817e-04, -3.10810969e-04, -3.35456127e-04,
       -3.40220719e-04, -4.12029046e-04, -4.07599211e-04, -3.82695819e-04,
       -3.51907149e-04, -3.75929475e-04, -3.65198995e-04, -3.48092723e-04,
       -3.90542364e-04, -2.62700013e-04, -3.27245199e-04, -2.94906342e-04,
       -3.53191418e-04, -3.64502986e-04, -4.36597205e-04, -4.36648251e-04,
       -3.58540794e-04, -4.16593127e-04, -3.91759561e-04, -4.12911572e-04,
       -4.41245691e-04, -4.39755909e-04, -4.40685758e-04, -4.05245889e-04,
       -3.67137167e-04, -3.13569319e-04, -3.16424144e-04, -3.76663055e-04,
       -3.05839539e-04, -2.82310361e-04, -3.16559950e-04, -2.65865632e-04,
       -2.11311514e-04, -2.43482269e-04, -2.04985503e-04, -1.89300573e-04,
       -2.20181552e-04, -2.83322280e-04, -2.30412829e-04, -1.92327838e-04,
       -1.93217781e-04, -3.19652788e-04, -3.53802486e-04, -2.49373242e-04,
       -2.39961054e-04, -

In [ ]:
# a = np.array([1,5,10,15,16,20])
a = np.append(a, [4])
print(a[1:7])
# np.mean(a)

In [ ]:
a = np.array([1,5,10,15,16,20])
b = np.array([1,2,3,4,5,6])
c = np.dot(a,b)
# print(np.dot(a,b))
d = np.array([1,2,3,4,5,6])
e = c * d
# print(c)
# print(e)
print(b*d)

In [ ]:
120+80+60+30+10+1

In [ ]:
z = np.array([.5,.6,1.2,5.6,2.6])
print(a.shape)
z.tofile('./example.txt',sep="\n",format="%s")

In [ ]:
print(frameCount)